**All Packages Used**

In [31]:
import pandas as pd
from scipy.spatial import cKDTree
import folium
import requests
from folium.plugins import MarkerCluster

**DATA**

In [32]:
climbs = pd.read_csv('utah_climbs.csv')
weather = pd.read_csv('Utah_Weather_Stations.csv')
#weather.head()
#climbs.head()

# **Combining Based on Closest Location**

In [13]:
# Sample DataFrames
df1 = pd.DataFrame({
    'latitude': [40.7128, 34.0522, 37.7749],
    'longitude': [-74.0060, -118.2437, -122.4194],
    'data1': ['A', 'B', 'C']
})

df2 = pd.DataFrame({
    'latitude': [41.8781, 34.0522, 37.7749],
    'longitude': [-87.6298, -118.2437, -122.4194],
    'data2': [1, 2, 3]
})

# Create KDTree for df2
tree = cKDTree(df2[['latitude', 'longitude']])

# Function to find closest point in df2 for each row in df1
def find_closest(row):
    distance, index = tree.query([row['latitude'], row['longitude']])
    closest_data = df2.iloc[index]
    return pd.Series({'data2': closest_data['data2'], 'distance': distance})

# Apply the function to each row in df1
result = df1.apply(find_closest, axis=1)

# Combine the results with df1
combined_df = pd.concat([df1, result], axis=1)

print(combined_df)


   latitude  longitude data1  data2   distance
0   40.7128   -74.0060     A    1.0  13.673546
1   34.0522  -118.2437     B    2.0   0.000000
2   37.7749  -122.4194     C    3.0   0.000000


**Updated and Shortened dataframes**

In [34]:
climbs = climbs.rename(columns={'Area Latitude': 'latitude', 'Area Longitude': 'longitude'})
weather = weather.rename(columns={'LATITUDE': 'latitude', 'LONGITUDE': 'longitude'})
test_climb = climbs[['Route', 'latitude', 'longitude']]
test_weather = weather[['STATION_NA', 'latitude', 'longitude']]
merge_climb = test_climb.head(1000)
merge_weather = test_weather.head(100)

**cKD Tree**

In [45]:
def merge_data_dist(df1, df2, keep_col, lat = 'Latitude', lon = 'Longitude'):
    # Rename the df to correct column names
    df1 = df1.rename(columns={lat: 'Latitude', lon: 'Longitude'})
    df2 = df2.rename(columns={lat: 'Latitude', lon: 'Longitude'})
    
    # Create KDTree for df2
    tree = cKDTree(df2[['Latitude', 'Longitude']])
    
    # Function to find closest point in df2 for each row in df1
    def find_closest(row):
        distance, index = tree.query([row['Latitude'], row['Longitude']])
        closest_data = df2.iloc[index]
        return pd.Series({keep_col: closest_data[keep_col], 'Distance': distance})

    # Apply the function to each row in df1
    closest = df1.apply(find_closest, axis=1)
    
    # Combine the results with df1
    merged = pd.concat([df1, closest], axis=1)

    return merged

#test = merge_data_dist(weather, climbs, 'Route', lat = 'latitude', lon = 'longitude')
ckd_merge = merge_data_dist(merge_climb, merge_weather, 'STATION_NA', lat = 'latitude', lon = 'longitude')
print(ckd_merge)

                    Route  Latitude  Longitude          STATION_NA  Distance
0                Tiki Man  38.49691 -109.31021         CEDAR POINT  1.098183
1            The Bleeding  38.49691 -109.31021         CEDAR POINT  1.098183
2                Doubloon  38.49691 -109.31021         CEDAR POINT  1.098183
3             Prosthetics  38.49649 -109.31053         CEDAR POINT  1.097851
4           Donut Project  38.49649 -109.31053         CEDAR POINT  1.097851
..                    ...       ...        ...                 ...       ...
995          Kermit's Wad  40.57380 -111.75490  BRYCE CANYON NP HQ  3.212390
996         Leggo My Eggo  40.57405 -111.76875  BRYCE CANYON NP HQ  3.211181
997     The Pabst Schmear  40.57399 -111.76119  BRYCE CANYON NP HQ  3.211910
998       Fish For Brains  40.57399 -111.76119  BRYCE CANYON NP HQ  3.211910
999  Barefoot in Barbados  40.57390 -111.75620  BRYCE CANYON NP HQ  3.212350

[1000 rows x 5 columns]


In [43]:
print(ckd_merge['STATION_NA'].unique())
ckd_merge.head()

['CEDAR POINT' 'BRYCE CANYON NP HQ' 'FOUR MILE BENCH' '40 MILE RIDGE'
 'ALTON' 'CENTRAL' 'St. George' 'BADGER SPRING' 'BEAVER DAM SLOPE'
 'HURRICANE' 'BUCKSKIN MOUNTAIN' 'BLANDING' 'COAL CREEK NEAR CEDAR CITY'
 'SEVIER RIVER/HATCH' 'LAVA POINT RAWS' 'ZION CANYON' 'ZION NATIONAL PARK'
 'CEDAR CITY STEAM PLA' 'SAINT GEORGE' 'GUNLOCK POWERHOUSE'
 'VEYO POWERHOUSE' 'SANTA CLARA RIVER/GUNLOCK' 'GARDNER PEAK'
 'ST GEORGE FD' 'PINE VALLEY' 'CEDAR CITY 5E' 'GLENDALE' 'EASTFORK/VIRGIN'
 'ST GEORGE' 'BLUFF']


Route  Latitude  Longitude   STATION_NA  Distance
0       Tiki Man  38.49691 -109.31021  CEDAR POINT  1.098183
1   The Bleeding  38.49691 -109.31021  CEDAR POINT  1.098183
2       Doubloon  38.49691 -109.31021  CEDAR POINT  1.098183
3    Prosthetics  38.49649 -109.31053  CEDAR POINT  1.097851
4  Donut Project  38.49649 -109.31053  CEDAR POINT  1.097851

In [15]:
# Create KDTree for df2
tree = cKDTree(weather[['Area Latitude', 'Area Longitude']])

# Function to find closest point in df2 for each row in df1
def find_closest(row):
    distance, index = tree.query([row['Area Latitude'], row['Area Longitude']])
    closest_data = weather.iloc[index]
    return pd.Series({'STATION_NA': closest_data['STATION_NA'], 'distance': distance})

# Apply the function to each row in df1
closest = climbs.apply(find_closest, axis=1)

# Combine the results with df1
merged = pd.concat([climbs, closest], axis=1)

merged

Route  \
0                             Tiki Man   
1                         The Bleeding   
2                             Doubloon   
3                          Prosthetics   
4                        Donut Project   
...                                ...   
6102                        Suavemente   
6103                    The Indecisive   
6104                           Crack 6   
6105  Pre-pubescent Pimpled Tortoises.   
6106            They Call Him Flinters   

                                                    URL  Avg Stars Rating  \
0     https://www.mountainproject.com/route/10571855...        4.0  5.13c   
1     https://www.mountainproject.com/route/10813817...        4.0  5.14b   
2     https://www.mountainproject.com/route/11953024...        3.0  5.14b   
3     https://www.mountainproject.com/route/11288012...        4.0  5.13d   
4     https://www.mountainproject.com/route/11607613...        3.0  5.14+   
...                                                 ...        ...    ...   
6102  https://www.mountainproject.com/route/12500311...        2.3    5.8   
6103  https://www.mountainproject.com/route/12508882...        2.0    5.8   
6104  https://www.mountainproject.com/route/12333204...        2.5   5.8+   
6105  https://www.mountainproject.com/route/12063800...        3.0    5.7   
6106  https://www.mountainproject.com/route/12081882...        3.0    5.7   

      Pitches  Length  Area Latitude  Area Longitude   PG13      R  ...  \
0           1    60.0       38.49691      -109.31021  False  False  ...   
1           1    60.0       38.49691      -109.31021  False  False  ...   
2           1    90.0       38.49691      -109.31021  False  False  ...   
3           1    90.0       38.49649      -109.31053  False  False  ...   
4           1    30.0       38.49649      -109.31053  False  False  ...   
...       ...     ...            ...             ...    ...    ...  ...   
6102        1    50.0       40.69886      -110.89815  False  False  ...   
6103        1    50.0       40.69886      -110.89815  False  False  ...   
6104        1    40.0       40.59798      -109.73133  False  False  ...   
6105        1    30.0       40.89100      -109.76765  False  False  ...   
6106        1    90.0       40.90656      -109.79332  False  False  ...   

     numVotes numViews  Year ViewsPerMonth             Shared_by  Month  Day  \
0          11     9559  2004            42      Anonymous Coward     12   31   
1           2     6238  2013            49              Orphaned      5   12   
2           1      953  2020            25          Ben Crawford      9    9   
3           4     2868  2017            36            ben jammin      5    7   
4           1     1560  2018            26             j wharton     11    8   
...       ...      ...   ...           ...                   ...    ...  ...   
6102        3       51  2023            42  The Possum's Protégé      9   25   
6103        2       44  2023            44          Craig Martin     10    9   
6104        2       69  2022             6              Joe Kitz     10   27   
6105        1      348  2021            11                Paully      5    1   
6106        1      312  2021            11                Paully      6    3   

            Date   STATION_NA      distance  
0     2004-12-31  CEDAR POINT  1.294648e+07  
1     2013-05-12  CEDAR POINT  1.294648e+07  
2     2020-09-09  CEDAR POINT  1.294648e+07  
3     2017-05-07  CEDAR POINT  1.294648e+07  
4     2018-11-08  CEDAR POINT  1.294648e+07  
...          ...          ...           ...  
6102  2023-09-25  CEDAR POINT  1.294649e+07  
6103  2023-10-09  CEDAR POINT  1.294649e+07  
6104  2022-10-27  CEDAR POINT  1.294649e+07  
6105  2021-05-01  CEDAR POINT  1.294649e+07  
6106  2021-06-03  CEDAR POINT  1.294649e+07  

[6107 rows x 32 columns]

**Geopy Distance**

In [44]:
from geopy.distance import geodesic

def find_closest(row):
    coordinates1 = (row['latitude'], row['longitude'])
    
    # Calculate distances using Haversine formula and find the minimum
    distances = merge_weather.apply(lambda x: geodesic(coordinates1, (x['latitude'], x['longitude'])).miles, axis=1)
    min_distance_index = distances.idxmin()
    
    # Get corresponding data from data2
    closest_place = merge_weather.loc[min_distance_index]
    
    # Combine data from data1 and closest_place
    return pd.concat([row, closest_place], ignore_index=True)

# Apply the function to each row in data1
geo_merge = merge_climb.apply(find_closest, axis=1)

# Rename columns in the merged DataFrame
geo_merge.columns = ['Route', 'latitude_data1', 'longitude_data1', 'STATION_NA', 'latitude_data2', 'longitude_data2']

# Display the merged DataFrame
print(geo_merge)

                    Route  latitude_data1  longitude_data1   STATION_NA  \
0                Tiki Man        38.49691       -109.31021  CEDAR POINT   
1            The Bleeding        38.49691       -109.31021  CEDAR POINT   
2                Doubloon        38.49691       -109.31021  CEDAR POINT   
3             Prosthetics        38.49649       -109.31053  CEDAR POINT   
4           Donut Project        38.49649       -109.31053  CEDAR POINT   
..                    ...             ...              ...          ...   
995          Kermit's Wad        40.57380       -111.75490        ALTON   
996         Leggo My Eggo        40.57405       -111.76875        ALTON   
997     The Pabst Schmear        40.57399       -111.76119        ALTON   
998       Fish For Brains        40.57399       -111.76119        ALTON   
999  Barefoot in Barbados        40.57390       -111.75620        ALTON   

     latitude_data2  longitude_data2  
0         37.430000      -109.050000  
1         37.430000  

In [48]:
import math
x = 40.57390 - 37.433333
y = -111.7562 - -112.48333
dist = math.sqrt(x**2 + y**2)
dist

3.2236437641881293

In [39]:
print(geo_merge['STATION_NA'].unique())
geo_merge.head()

['CEDAR POINT' 'ALTON' 'BRYCE CANYON NP HQ' '40 MILE RIDGE' 'CENTRAL'
 'St. George' 'BADGER SPRING' 'BEAVER DAM SLOPE' 'VIRGIN RIVER/HURR 6W'
 'BUCKSKIN MOUNTAIN' 'BLANDING' 'COAL CREEK NEAR CEDAR CITY'
 'LAVA POINT RAWS' 'ZION CANYON' 'ZION NATIONAL PARK'
 'CEDAR CITY STEAM PLA' 'GUNLOCK POWERHOUSE' 'SAINT GEORGE'
 'VEYO POWERHOUSE' 'SANTA CLARA RIVER/GUNLOCK' 'GARDNER PEAK'
 'ST GEORGE FD' 'PINE VALLEY' 'GLENDALE' 'EASTFORK/VIRGIN' 'ST GEORGE']


Route  latitude_data1  longitude_data1   STATION_NA  \
0       Tiki Man        38.49691       -109.31021  CEDAR POINT   
1   The Bleeding        38.49691       -109.31021  CEDAR POINT   
2       Doubloon        38.49691       -109.31021  CEDAR POINT   
3    Prosthetics        38.49649       -109.31053  CEDAR POINT   
4  Donut Project        38.49649       -109.31053  CEDAR POINT   

   latitude_data2  longitude_data2  
0           37.43          -109.05  
1           37.43          -109.05  
2           37.43          -109.05  
3           37.43          -109.05  
4           37.43          -109.05

In [ ]:
merge_weather

# **Mapping the data**

**Creating Map**

In [16]:
state_geo = requests.get(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_states.json"
).json()
state_data = pd.read_csv(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_unemployment_oct_2012.csv"
)

t = folium.Map(location=[48, -102], zoom_start=3)

folium.Choropleth(
    geo_data=state_geo,
    name="choropleth",
    data=state_data,
    columns=["State", "Unemployment"],
    key_on="feature.id",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Unemployment Rate (%)",
).add_to(t)
folium.Marker(
    location=[37.8, -113.6625],
    tooltip="Weather!",
    popup="Mt. Hood Meadows",
    icon=folium.Icon(icon="cloud"),
).add_to(t)

folium.LayerControl().add_to(t)
t

In [17]:
climbs.head()

Route                                                URL  \
0       Tiki Man  https://www.mountainproject.com/route/10571855...   
1   The Bleeding  https://www.mountainproject.com/route/10813817...   
2       Doubloon  https://www.mountainproject.com/route/11953024...   
3    Prosthetics  https://www.mountainproject.com/route/11288012...   
4  Donut Project  https://www.mountainproject.com/route/11607613...   

   Avg Stars Rating  Pitches  Length  Area Latitude  Area Longitude   PG13  \
0        4.0  5.13c        1    60.0       38.49691      -109.31021  False   
1        4.0  5.14b        1    60.0       38.49691      -109.31021  False   
2        3.0  5.14b        1    90.0       38.49691      -109.31021  False   
3        4.0  5.13d        1    90.0       38.49649      -109.31053  False   
4        3.0  5.14+        1    30.0       38.49649      -109.31053  False   

       R  ...  Mixed Rating_num numVotes numViews  Year  ViewsPerMonth  \
0  False  ...  False       13.6       11     9559  2004             42   
1  False  ...  False       14.4        2     6238  2013             49   
2  False  ...  False       14.4        1      953  2020             25   
3  False  ...  False       13.8        4     2868  2017             36   
4  False  ...  False       14.7        1     1560  2018             26   

          Shared_by  Month  Day        Date  
0  Anonymous Coward     12   31  2004-12-31  
1          Orphaned      5   12  2013-05-12  
2      Ben Crawford      9    9  2020-09-09  
3        ben jammin      5    7  2017-05-07  
4         j wharton     11    8  2018-11-08  

[5 rows x 30 columns]

In [18]:
icons = folium.Map(location=(40, -111), zoom_start=6.5, tiles="cartodb positron")

folium.Marker(
    location=[37.8, -113.6625],
    tooltip="Weather!",
    popup="Mt. Hood Meadows",
    icon=folium.Icon(icon="cloud"),
).add_to(icons)
folium.Marker(
    location=[40.2, -110.7113],
    tooltip="Info!",
    popup="Timberline Lodge",
    icon=folium.Icon(color="green"),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][0], climbs['Area Longitude'][0]],
    tooltip=climbs['Route'][0],
    popup=climbs['Rating'][0],
    icon=folium.Icon(prefix='fa', color="red", icon='hill-rockslide'),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][12], climbs['Area Longitude'][12]],
    tooltip=climbs['Route'][12],
    popup=climbs['Rating'][12],
    icon=folium.Icon(prefix='fa', icon="hill-rockslide"),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][20], climbs['Area Longitude'][20]],
    tooltip=climbs['Route'][20],
    popup=climbs['Rating'][20],
    icon=folium.Icon(icon="thumbs-up"),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][300], climbs['Area Longitude'][300]],
    tooltip=climbs['Route'][300],
    popup=climbs['Rating'][300],
    icon=folium.Icon(icon="thumbs-down"),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][100], climbs['Area Longitude'][100]],
    tooltip=climbs['Route'][100],
    popup=climbs['Rating'][100],
    icon=folium.Icon(icon="star"),
).add_to(icons)
folium.Marker(
    location=[climbs['Area Latitude'][1000], climbs['Area Longitude'][1000]],
    tooltip=climbs['Route'][1000],
    popup=climbs['Rating'][1000],
    icon=folium.Icon(prefix='fa', icon="star"),
).add_to(icons)

icons

In [19]:
map_center = [climbs['Area Latitude'].mean(), climbs['Area Longitude'].mean()]
utah_map = folium.Map(location=map_center, zoom_start=6.5)

# Create a MarkerCluster object
marker_cluster = MarkerCluster().add_to(utah_map)

# Add markers to the map using data from the DataFrame
for index, row in climbs.iterrows():
    folium.Marker([row['Area Latitude'], row['Area Longitude']], popup=row['Route'], icon=folium.Icon(prefix='fa', icon='star')).add_to(marker_cluster)

# Save the map as an HTML file
utah_map.save('map.html')
utah_map

In [27]:
climbs.head()

Route                                                URL  \
0       Tiki Man  https://www.mountainproject.com/route/10571855...   
1   The Bleeding  https://www.mountainproject.com/route/10813817...   
2       Doubloon  https://www.mountainproject.com/route/11953024...   
3    Prosthetics  https://www.mountainproject.com/route/11288012...   
4  Donut Project  https://www.mountainproject.com/route/11607613...   

   Avg Stars Rating  Pitches  Length  Area Latitude  Area Longitude   PG13  \
0        4.0  5.13c        1    60.0       38.49691      -109.31021  False   
1        4.0  5.14b        1    60.0       38.49691      -109.31021  False   
2        3.0  5.14b        1    90.0       38.49691      -109.31021  False   
3        4.0  5.13d        1    90.0       38.49649      -109.31053  False   
4        3.0  5.14+        1    30.0       38.49649      -109.31053  False   

       R  ...  Mixed Rating_num numVotes numViews  Year  ViewsPerMonth  \
0  False  ...  False       13.6       11     9559  2004             42   
1  False  ...  False       14.4        2     6238  2013             49   
2  False  ...  False       14.4        1      953  2020             25   
3  False  ...  False       13.8        4     2868  2017             36   
4  False  ...  False       14.7        1     1560  2018             26   

          Shared_by  Month  Day        Date  
0  Anonymous Coward     12   31  2004-12-31  
1          Orphaned      5   12  2013-05-12  
2      Ben Crawford      9    9  2020-09-09  
3        ben jammin      5    7  2017-05-07  
4         j wharton     11    8  2018-11-08  

[5 rows x 30 columns]

In [29]:
def clus_map(df, lat = 'Latitude', lon = 'Longitude', desc = 'Description', name = 'cluster_map'):
    # Rename the df to correct column names
    df = df.rename(columns={lat: 'Latitude', lon: 'Longitude', desc: 'Description'})
    
    map_center = [df['Latitude'].mean(), df['Longitude'].mean()]
    map = folium.Map(location=map_center, zoom_start=6.5)

    # Create a MarkerCluster object
    marker_cluster = MarkerCluster().add_to(map)

    # Add markers to the map using data from the DataFrame
    for index, row in df.iterrows():
        folium.Marker([row['Latitude'], row['Longitude']], popup=row['Description'], icon=folium.Icon(prefix='fa', icon='star')).add_to(marker_cluster)

    # Save the map as an HTML file
    map.save(f'{name}.html')

#clus_map(climbs, desc='Route', name='blank')
clus_map(climbs, 'Area Latitude', 'Area Longitude', 'Route', 'full')

**This is the heatmap section**

In [9]:
from folium.plugins import HeatMap

data = climbs[['Area Latitude', 'Area Longitude']].values.tolist()

map_center = [climbs['Area Latitude'].mean(), climbs['Area Longitude'].mean()]
heat_map = folium.Map(location=map_center, zoom_start=6.5)
HeatMap(data).add_to(heat_map)

heat_map

In [1]:
# Geopy example
import pandas as pd
from geopy.distance import geodesic

# Sample data for data1 DataFrame
data1 = {
    'name': ['Location A', 'Location B', 'Location C'],
    'latitude': [40.7128, 34.0522, 37.7749],
    'longitude': [-74.0060, -118.2437, -122.4194]
}

# Sample data for data2 DataFrame
data2 = {
    'place': ['Place X', 'Place Y', 'Place Z'],
    'latitude': [35.6895, 41.8781, 33.6844],
    'longitude': [139.6917, -87.6298, -117.8265]
}

# Creating DataFrames
data1 = pd.DataFrame(data1)
data2 = pd.DataFrame(data2)

# Function to find the closest place in data2 for each row in data1
def find_closest(row):
    coordinates1 = (row['latitude'], row['longitude'])
    
    # Calculate distances using Haversine formula and find the minimum
    distances = data2.apply(lambda x: geodesic(coordinates1, (x['latitude'], x['longitude'])).miles, axis=1)
    min_distance_index = distances.idxmin()
    
    # Get corresponding data from data2
    closest_place = data2.loc[min_distance_index]
    
    # Combine data from data1 and closest_place
    return pd.concat([row, closest_place], ignore_index=True)

# Apply the function to each row in data1
merged_data = data1.apply(find_closest, axis=1)

# Rename columns in the merged DataFrame
merged_data.columns = ['name', 'latitude_data1', 'longitude_data1', 'place', 'latitude_data2', 'longitude_data2']

# Display the merged DataFrame
print("Merged DataFrame:")
print(merged_data)


Merged DataFrame:
         name  latitude_data1  longitude_data1    place  latitude_data2  \
0  Location A         40.7128         -74.0060  Place Y         41.8781   
1  Location B         34.0522        -118.2437  Place Z         33.6844   
2  Location C         37.7749        -122.4194  Place Z         33.6844   

   longitude_data2  
0         -87.6298  
1        -117.8265  
2        -117.8265  


In [17]:
climbs = climbs.rename(columns={'Area Latitude': 'latitude', 'Area Longitude': 'longitude'})
weather = weather.rename(columns={'LATITUDE': 'latitude', 'LONGITUDE': 'longitude'})
merge_climb = climbs[['Route', 'latitude', 'longitude']]
merge_weather = weather[['STATION_NA', 'latitude', 'longitude']]
merge_climb = merge_climb.head(1000)
merge_weather = merge_weather.head(100)
len(merge_weather)

100

In [12]:
from geopy.distance import geodesic

def normalize_latitude(lat):
    return lat % 180 - 90

# Function to find the closest place in data2 for each row in data1
def find_closest(row):
    coordinates1 = (normalize_latitude(row['latitude']), row['longitude'])
    
    # Calculate distances using Haversine formula and find the minimum
    distances = merge_weather.apply(lambda x: geodesic(coordinates1, (normalize_latitude(x['latitude']), x['longitude'])).miles, axis=1)
    min_distance_index = distances.idxmin()
    
    # Get corresponding data from data2
    closest_place = merge_weather.loc[min_distance_index]
    
    # Combine data from data1 and closest_place
    return pd.concat([row, closest_place], ignore_index=True)

# Apply the function to each row in data1
merged_data = merge_climb.apply(find_closest, axis=1)

# Rename columns in the merged DataFrame
merged_data.columns = ['name', 'latitude_data1', 'longitude_data1', 'place', 'latitude_data2', 'longitude_data2']

#

KeyboardInterrupt: 

In [22]:
out_of_range_df = merge_climb[(merge_climb['latitude'] < -90) | (merge_climb['latitude'] > 90)]

# Print the rows with latitude outside the range
print("Rows with latitude outside the range -90 to 90:")
print(out_of_range_df)

Rows with latitude outside the range -90 to 90:
Empty DataFrame
Columns: [Route, latitude, longitude]
Index: []


In [23]:
out_of_range_df = merge_weather[(merge_weather['latitude'] < -90) | (merge_weather['latitude'] > 90)]

# Print the rows with latitude outside the range
print("Rows with latitude outside the range -90 to 90:")
print(out_of_range_df)

Rows with latitude outside the range -90 to 90:
                       STATION_NA      latitude     longitude
0                          CANNAN -1.257919e+07  4.439105e+06
1          FORT PEARCE /ST GEORGE -1.261042e+07  4.439189e+06
2     VIRGIN RIVER/ST GEORGE 10SW -1.262424e+07  4.439830e+06
3         KANAB MUNICIPAL AIRPORT -1.252687e+07  4.440500e+06
4                  CW2921 Hildale -1.257535e+07  4.441154e+06
...                           ...           ...           ...
1547                     LEWISTON -1.244932e+07  5.155978e+06
1548         BEAR LAKE STATE PARK -1.240108e+07  5.155978e+06
1549               DMAD RESERVOIR -1.235655e+07  5.160971e+06
1550                  FLINT CREEK -1.248732e+07  5.172161e+06
1551                       LIFTON -1.239759e+07  5.174937e+06

[1552 rows x 3 columns]
